In [1]:
import yfinance as yf
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.model_selection import train_test_split
from sklearn.svm import SVR
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
import matplotlib.pyplot as plt
from datetime import datetime, timedelta

# 获取数据
def get_data(ticker_symbol, start_date, end_date):
    ticker_data = yf.Ticker(ticker_symbol)
    data = ticker_data.history(start=start_date, end=end_date)
    return data['Close'].values, data.index

# 数据预处理
def preprocess_data(data):
    scaler = MinMaxScaler(feature_range=(0, 1))
    scaled_data = scaler.fit_transform(data.reshape(-1, 1))
    return scaled_data, scaler

# 创建数据集
def create_dataset(data, look_back=1):
    dataX, dataY = [], []
    for i in range(len(data) - look_back - 1):
        a = data[i:(i + look_back), 0]
        dataX.append(a)
        dataY.append(data[i + look_back, 0])
    return np.array(dataX), np.array(dataY)

# 定义模型
def build_lstm_model(input_shape):
    model = Sequential()
    model.add(LSTM(50, return_sequences=True, input_shape=input_shape))
    model.add(LSTM(50))
    model.add(Dense(1))
    model.compile(optimizer='adam', loss='mean_squared_error')
    return model

# 预测未来值
def predict_future(model, data, num_predictions, look_back):
    predictions = []
    current_batch = data[-look_back:]
    for i in range(num_predictions):
        current_pred = model.predict(current_batch[np.newaxis, :, :])[0]
        predictions.append(current_pred)
        current_batch = np.append(current_batch[1:], current_pred)
    return predictions

# 反归一化数据
def inverse_transform(scaler, data, shape):
    dummy = np.zeros(shape=(len(data), shape[1]))
    dummy[:,0] = data[:,0]
    return scaler.inverse_transform(dummy)[:,0]

# 绘图函数
def plot_predictions(real_prices, predicted_prices, dates):
    plt.plot(dates, real_prices, label='Real Prices', color='red', marker='o')
    plt.plot(dates, predicted_prices, label='Predicted Prices', color='blue', linestyle='--', marker='o')
    plt.title('Stock Price Prediction')
    plt.xlabel('Date')
    plt.ylabel('Price')
    plt.legend()
    plt.show()

# 主函数
def main():
    # 参数设置
    ticker_symbol = 'AAPL'
    start_date = '2020-01-01'
    end_date = '2023-01-01'
    look_back = 5
    
    # 获取和预处理数据
    data, dates = get_data(ticker_symbol, start_date, end_date)
    data_scaled, scaler = preprocess_data(data)
    
    # 创建数据集
    X, y = create_dataset(data_scaled, look_back)
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)
    
    # 重塑输入以作为LSTM输入
    X_train = X_train.reshape((X_train.shape[0], X_train.shape[1], 1))
    X_test = X_test.reshape((X_test.shape[0], X_test.shape[1], 1))
    
    # 建立LSTM模型
    lstm_model = build_lstm_model((X_train.shape[1], 1))
    lstm_model.fit(X_train, y_train, epochs=5, batch_size=1, verbose=1)
    
    # 预测
    predictions = predict_future(lstm_model, data_scaled, 10, look_back)
    
    # 反归一化预测
    predictions = np.array(predictions)
    predictions = inverse_transform(scaler, predictions.reshape(-1, 1), data_scaled.shape)
    
    
    # 绘制预测和实际价格
    plot_predictions(data[-10:], predictions, dates[-10:])

if __name__ == '__main__':
    main()


Epoch 1/5
600/600 [==============================] - 6s 5ms/step - loss: 0.0091
Epoch 2/5
600/600 [==============================] - 3s 5ms/step - loss: 0.0022
Epoch 3/5
600/600 [==============================] - 3s 5ms/step - loss: 0.0019
Epoch 4/5
600/600 [==============================] - 3s 5ms/step - loss: 0.0019
Epoch 5/5
1/1 [==============================] - 1s 1s/step


IndexError: too many indices for array: array is 1-dimensional, but 2 were indexed